In [1]:
# gain#2 w/o D.B.
import ROOT as r
import numpy as np
%jsroot

r.gROOT.ProcessLine(".x ../../rootlogon.C")

file_path = '../../ROOT/test0046.root'
root_file = r.TFile(file_path)

add include path : /home/exp/ANAROOT/anaroot/include
reading libXMLParser.so
reading libananadeko.so
reading libanacore.so
reading libanabrips.so
reading libanadali.so
reading libanasamurai.so
reading libanacatana.so
reading libanaespri.so
reading libanawinds.so
reading libanaloop.so
reading libanaloopexample.so
reading libanaloopencexample.so


In [2]:
r.tree.Draw("F7IC_Eraw[0]>>h0(8e2,0,8e3)")
r.tree.Draw("F7IC_Eraw[1]>>h1(8e2,0,8e3)")
r.tree.Draw("F7IC_Eraw[2]>>h2(8e2,0,8e3)")
r.tree.Draw("F7IC_Eraw[3]>>h3(8e2,0,8e3)")
r.tree.Draw("F7IC_Eraw[4]>>h4(8e2,0,8e3)")
r.tree.Draw("F7IC_Eraw[5]>>h5(8e2,0,8e3)")

r.zone(3, 2)
r.ht(1,6)

r.c1.Draw()


 Draw ID:1
 Draw ID:2
 Draw ID:3
 Draw ID:4
 Draw ID:5
 Draw ID:6


Info in <TCanvas::MakeDefCanvas>:  created default TCanvas with name c1


In [3]:
# キャンバスを作成 (6C2 = 15通りなので3x5に分割)
c2D = r.TCanvas("c2D", "2D Histograms", 1500, 900)
c2D.Divide(3, 5)

# 組み合わせを保存するリスト
hist2D_list = []

# すべての組み合わせ（6C2 = 15通りの組み合わせ）
comb_list = [(0, 1), (0, 2), (0, 3), (0, 4), (0, 5), 
             (1, 2), (1, 3), (1, 4), (1, 5), 
             (2, 3), (2, 4), (2, 5), 
             (3, 4), (3, 5), 
             (4, 5)]

for idx, (i, j) in enumerate(comb_list):
    # 2次元ヒストグラムを描画
    hist_name = f"h2D_{i}_{j}"
    draw_cmd = f"F7IC_Eraw[{i}]:F7IC_Eraw[{j}]>>{hist_name}(2000,0,8000,2000,0,8000)"
    r.tree.Draw(draw_cmd, "", "COLZ")
    
    # キャンバスに描画
    c2D.cd(idx+1)
    r.gPad.SetLogz()
    
    # ヒストグラムを取得
    hist2D = r.gDirectory.Get(hist_name)
    hist2D_list.append(hist2D)
    
    # ヒストグラムを描画
    hist2D.Draw("COLZ")

# 更新して表示
c2D.Update()


In [4]:
def find_peaks(hist, threshold=250):
    spec = r.TSpectrum()
    npeaks = spec.Search(hist, 2, "", threshold)
    
    peaks = []
    fits = []  # Store fit results here
    
    for i in range(npeaks):
        x = spec.GetPositionX()[i]
        bin = hist.FindBin(x)
        sigma = 40 
        
        fit_range = 2.5 * sigma
        
        fit = r.TF1(f"fit_{i}", "gaus", x - fit_range, x + fit_range)
        hist.Fit(fit, "RQ0")
        
        peak_x = fit.GetParameter(1)
        peak_sigma = fit.GetParameter(2)
        
        peaks.append((peak_x, peak_sigma))
        fits.append(fit)  # Append the fit object to the list
    
    peaks.sort(key=lambda peak: peak[0])
    
    return peaks, fits

expected_x = [50, 100, 150, 200, 250, 300, 350, 400, 450, 500, 550, 600, 700, 800, 900, 1000, 1100]

# Initialize canvases for each type of graph (3x2 grid)
cPeak = r.TCanvas("cPeak", "Peak Graphs", 1200, 800)
cPeak.Divide(3, 2)

cRes = r.TCanvas("cRes", "Residual Graphs", 1200, 800)
cRes.Divide(3, 2)

cPer = r.TCanvas("cPer", "Percentage Error Graphs", 1200, 800)
cPer.Divide(3, 2)

cHwF = r.TCanvas("cHwF", "Hist with Gauss Fits", 1200, 800)
cHwF.Divide(3, 2)

graphs = []
percentage_error_graphs = []
residual_graphs = []
fit_results = []  # Store the gauss fits for saving later
hists_with_fits = []  # Store histograms with fits for saving later

for i in range(6):
    hist = r.gDirectory.Get(f"h{i}")
    peaks, fits = find_peaks(hist)

    # Make a copy of the histogram to add all gauss fits
    hist_with_fits = hist.Clone(f"hist_with_fits_h{i}")
    
    x_values = []
    y_values = []
    y_errors = []
    
    for j, (x, sigma) in enumerate(peaks):
        if j < len(expected_x):
            x_values.append(expected_x[j])
            y_values.append(x)
            y_errors.append(sigma)
    
    n = len(x_values)
    graph = r.TGraphErrors(n, 
                           np.array(x_values, dtype=float), 
                           np.array(y_values, dtype=float), 
                           np.zeros(n), 
                           np.array(y_errors, dtype=float))
    
    graph.SetTitle(f"Peak Analysis for h{i}")
    graph.GetXaxis().SetTitle("Test input (mV)")
    graph.GetYaxis().SetTitle("MADC [ch]")
    graph.SetMarkerStyle(20)
    graph.SetMarkerColor(r.kBlue)
    graph.SetLineColor(r.kRed)
    
    # Draw PeakGraph in cPeak
    cPeak.cd(i+1)
    graph.Draw("AP")
    
    # Residuals calculation and plotting
    residuals = []
    for j in range(n):
        if x_values[j] <= 500:
            fitted_y = graph.Eval(x_values[j])
            residual = y_values[j] - fitted_y
            residuals.append(residual)

    if residuals:
        residual_graph = r.TGraph(len(residuals), 
                                   np.array(x_values[:len(residuals)], dtype=float), 
                                   np.array(residuals, dtype=float))
        residual_graph.SetTitle(f"Residuals for h{i}")
        residual_graph.GetXaxis().SetTitle("Pulser input [mV]")
        residual_graph.GetYaxis().SetTitle("Residuals")
        residual_graph.SetMarkerStyle(21)
        residual_graph.SetMarkerColor(r.kGreen)
        
        cRes.cd(i+1)
        residual_graph.Draw("AP")
        residual_graphs.append(residual_graph)

    # Percentage error calculation and plotting
    percentage_errors = []
    for j in range(n):
        percentage_error = (y_errors[j] / y_values[j]) * 100 if y_values[j] != 0 else 0
        percentage_errors.append(percentage_error)
    
    percentage_error_graph = r.TGraph(n, 
                                      np.array(x_values, dtype=float), 
                                      np.array(percentage_errors, dtype=float))
    percentage_error_graph.SetTitle(f"Percentage Error for h{i}")
    percentage_error_graph.GetXaxis().SetTitle("test input [mV]")
    percentage_error_graph.GetYaxis().SetTitle("Percentage Error (%)")
    percentage_error_graph.SetMarkerStyle(22)
    percentage_error_graph.SetMarkerColor(r.kRed)
    
    cPer.cd(i+1)  
    percentage_error_graph.Draw("AP")
    percentage_error_graphs.append(percentage_error_graph)

    # Draw histogram and gauss fits
    cHwF.cd(i+1)
    hist_with_fits.Draw("")  # Draw the histogram with error bars
    
    for fit in fits:
        fit.SetLineColor(r.kRed)
        fit.Draw("same")  # Draw each gauss fit on the same canvas
        
        # Extract gauss parameters from fit
        amplitude = fit.GetParameter(0)
        mean = fit.GetParameter(1)
        sigma = fit.GetParameter(2)
        
        # Create a new TF1 representing the gauss function
        gauss_function = r.TF1(f"gauss_{i}_{j}", "gaus", fit.GetXmin(), fit.GetXmax())
        gauss_function.SetParameters(amplitude, mean, sigma)
        
        # Add the gauss function to the histogram
        hist_with_fits.Add(gauss_function)
    
    hists_with_fits.append(hist_with_fits)
    
    graphs.append(graph)
    fit_results.append(fits)  # Store the fit results for each histogram

cPeak.Update()
cRes.Update()
cPer.Update()
cHwF.Update()

# Create a ROOT file to save all graphs and fits
output_file = r.TFile("../../ROOT/f7ic0004.root", "RECREATE")

# Save each graph to the ROOT file
for i, graph in enumerate(graphs):
    graph.Write(f"PeakGraph_h{i}")
    residual_graphs[i].Write(f"residual_PeakGraph_h{i}")
    percentage_error_graphs[i].Write(f"percentage_error_h{i}")
    
    # Save the histogram with all gauss fits drawn on it
    hists_with_fits[i].Write(f"hist_with_fits_h{i}")

    # Save all gauss fit results for each histogram
    for j, fit in enumerate(fit_results[i]):
        fit.Write(f"gauss_fit_h{i}_peak{j}")

# Save the combined canvases
cPeak.Write("cPeak")
cRes.Write("cRes")
cPer.Write("cPer")
cHwF.Write("cHwF")

# Close the ROOT file
output_file.Close()


Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
Warning in <TSpectrum::Search>: threshold must 0<threshold<1, threshold=0.05 assumed
